## Group No: 164

### Group Member Names:

1. Govind Singh Chauhan (2023ac05771@wilp.bits-pilani.ac.in)
2. Mayank Grover (2023AC05486@wilp.bits-pilani.ac.in)
3.
4.

### Solution

In [ ]:
# Import necessary libraries
import pandas as pd
import nltk
from nltk.corpus import stopwords
from nltk.tokenize import RegexpTokenizer, word_tokenize
from nltk.stem import WordNetLemmatizer
from collections import defaultdict, Counter
import re
import seaborn as sns
import matplotlib.pyplot as plt
import math

# Load necessary NLTK resources
nltk.download('stopwords')
nltk.download('punkt')
nltk.download('punkt_tab')
nltk.download('wordnet')

[nltk_data] Downloading package stopwords to /root/nltk_data...
[nltk_data]   Package stopwords is already up-to-date!
[nltk_data] Downloading package punkt to /root/nltk_data...
[nltk_data]   Package punkt is already up-to-date!
[nltk_data] Downloading package punkt_tab to /root/nltk_data...
[nltk_data]   Unzipping tokenizers/punkt_tab.zip.
[nltk_data] Downloading package wordnet to /root/nltk_data...
[nltk_data]   Package wordnet is already up-to-date!


True

--------------------------------------------------------------------------
**Step 1: Initial Analysis (3 marks)**

What to Do:

Analyse the text and count the frequency of trigrams (sequences of three consecutive words).

Identify the most frequent trigrams in the dataset.

Provide a brief explanation of why these trigrams occur frequently.

For example:
* Are they common phrases?
* Do they reflect the nature of the dataset?

Deliverables:
* A table or plot of the top 10 most frequent trigrams.
* A short paragraph explaining the context and relevance of these trigrams.

In [ ]:
# Load the dataset
from google.colab import drive
drive.mount('/content/drive')
file_path = '/content/drive/MyDrive/Colab Notebooks/Dataset.xlsx'
data = pd.ExcelFile(file_path)

# Check the sheet names to understand the structure of the file
data.sheet_names

# Load the data from the first sheet
df = data.parse('Sheet1')

# Display the first few rows to examine the structure and content of the dataset
df.head()

Drive already mounted at /content/drive; to attempt to forcibly remount, call drive.mount("/content/drive", force_remount=True).


ID                             Title  \
0  10  Canadian Society of Soil Science   
1   1              King Arthur's family   
2   6                 Ralitsa Vassileva   
3   2         Tom Mooney (rugby league)   
4   3                   Topal (surname)   

                                                 URL  \
0  https://en.wikipedia.org/wiki/Canadian_Society...   
1  https://en.wikipedia.org/wiki/King_Arthur's_fa...   
2    https://en.wikipedia.org/wiki/Ralitsa_Vassileva   
3  https://en.wikipedia.org/wiki/Tom_Mooney_(rugb...   
4      https://en.wikipedia.org/wiki/Topal_(surname)   

                                Introduction/Summary  \
0  The Canadian Society of Soil Science (CSSS) is...   
1                                                NaN   
2  Ralitsa B. Vassileva (Bulgarian: Ралица Василе...   
3                                                NaN   
4  Topal is a Turkish word meaning "lame" and may...   

                                                Body  \
0  Canadian non-profit organization\nCanadian Soc...   
1  Family\n\n\nArthur in William Henry Margetson'...   
2  Bulgarian journalist\nRalitsa VassilevaBornRal...   
3  Australian rugby league footballer\nFor other ...   
4  TopalPronunciationTurkish: [ˈtopaɫ]OriginWord/...   

                                   Sections/Headings  \
0  ['Contents', 'Administration[edit]', 'Publicat...   
1  ['Contents', 'Medieval Welsh tradition[edit]',...   
2  ['Contents', 'Career[edit]', 'Awards, honours ...   
3  ['Contents', 'Career[edit]', 'References[edit]...   
4  ['Contents', 'Surnames of contemporary people[...   

                                          References  \
0  ['https://archive.org/details/literatureofsoil...   
1  ['http://www.culhwch.info/index.html#footnote1...   
2  ['https://grady.uga.edu/faculty/vassileva/', '...   
3  ['http://www.yesterdayshero.com.au/PlayerProfi...   
4                                                 []   

                                          Categories  \
0  ['Soil and crop science organizations', 'Agric...   
1  ['Family of King Arthur', 'Legendary royal fam...   
2  ['1963 births', 'Living people', 'CNN people',...   
3  ['1952 births', 'Living people', 'Australian r...   
4          ['Surnames', 'Turkish-language surnames']   

                                             Infobox  
0  {'Abbreviation': 'CSSS', 'Formation': '1954[1]...  
1                                                 {}  
2  {'Born': 'Ralitsa Vassileva (1963-06-08) 8 Jun...  
3  {'Born': '(1952-03-16) 16 March 1952 (age\xa07...  
4  {'Pronunciation': 'Turkish: [ˈtopaɫ]', 'Word/n...

**Description:**

>From the dataset preview, we can see that there are several columns:
>
>1. **Title**: This contains titles of articles, as it is typically short text, so might not provide rich context for trigram generation.
>2. **Introduction/Summary**: This seems like a promising column. It could contain brief, informative summaries of the articles, ideal for trigram extraction.
>3. **Body**: This is the main body of the text and would provide the most substantial content for trigram generation.
>4. **Sections/Headings**: This column contains lists of sections and headings, which is not be ideal for trigram modeling as it's more structured.
>5. **References**: Contains URLs and references, which are not useful for the trigram model.
>6. **Categories**: Similar to "Sections/Headings," this is more metadata and less useful for language modeling.
>7. **Infobox**: This contains structured data, which isn’t useful for trigram modeling.
>
>**Decision:**
>- We will focus on the **"Body"** and **"Introduction/Summary"** columns for text analysis and trigram modeling. These contain the actual content of the articles and should provide enough data for trigram extraction.<br />
><br />

In [ ]:
# Select relevant columns for analysis: 'Body' and 'Introduction/Summary'
df_text = df[['Introduction/Summary', 'Body']]

# Combine the text from both columns into a single text block for analysis
text_data = ' '.join(df_text['Introduction/Summary'].dropna()) + ' ' + ' '.join(df_text['Body'].dropna())

# Clean text: Remove URLs, special characters, numbers, and extra whitespace
cleaned_text = re.sub(r'http\S+', '', text_data)  # Remove URLs
cleaned_text = re.sub(r'[^\w\s]', '', cleaned_text)  # Remove punctuation
cleaned_text = re.sub(r'[^A-Za-z\s]', '', cleaned_text)  # Remove numbers and special characters (keep only letters)
cleaned_text = cleaned_text.lower()  # Convert to lowercase
cleaned_text = re.sub(r'\s+', ' ', cleaned_text).strip()  # Remove extra spaces

# Generate trigrams
trigrams = list(nltk.ngrams(cleaned_text.split(), 3))

# Count trigram frequencies
trigram_counts = Counter(trigrams)

# Convert trigrams from tuple to string (e.g., ('word1', 'word2', 'word3') -> 'word1 word2 word3')
trigram_counts_str = [(f'{w1} {w2} {w3}', count) for (w1, w2, w3), count in trigram_counts.items()]

# Display top 10 most frequent trigrams
top_10_trigrams = sorted(trigram_counts_str, key=lambda x: x[1], reverse=True)[:10]

print("Top 10 Trigrams:")
for trigram, freq in top_10_trigrams:
    print(f'- {trigram}: {freq}')
print("\n\n")

# Create a DataFrame for plotting
trigram_df = pd.DataFrame(top_10_trigrams, columns=['Trigram', 'Frequency'])

# Plotting the top 10 most frequent trigrams
sns.barplot(y='Trigram', x='Frequency', data=trigram_df)
plt.xticks(rotation=45, ha='right')
plt.title("Top 10 Most Frequent Trigrams")
plt.show()

Top 10 Trigrams:
- from the original: 4438
- archived from the: 4360
- the original on: 4175
- a b c: 2155
- you can help: 1562
- can help wikipedia: 1426
- help wikipedia by: 1426
- wikipedia by expanding: 1426
- is a stub: 1425
- a stub you: 1425





>The top 10 most frequent trigrams have been correctly identified, and the bar chart visualizes the results well.
>
>**Explanation:**
>
>1. **"from the original"**, **"archived from the"**, and **"the original on"** are among the most frequent trigrams, suggesting that these are common phrases in the dataset. This points to references to original sources or archived content, which is typical of data related to **Wikipedia articles** or similar types of content where the original and archived versions of pages are frequently discussed.
>
>2. **"a b c"**, **"you can help"**, **"can help wikipedia"**, and similar trigrams seem more domain-specific. These are likely to be calls to action or instructions related to contributing to **Wikipedia**. The dataset seems to include content that encourages users to contribute or expand articles, which is reflected in these repeated trigrams.
>
>3. **"is a stub"** and **"a stub you"** are also frequent, further supporting the idea that the dataset is related to **Wikipedia** articles. In Wikipedia, a "stub" refers to an article that is incomplete and requires expansion, indicating that the dataset may be involved in discussions around improving or expanding Wikipedia entries.<br />
><br />

-------------------------------------------------------------------------

#### Step 2: Data Preparation

What to Do:
1. Tokenize the text into words:
 * Split sentences into tokens (words).
 * Handle punctuation, case sensitivity, and special characters.
2. Generate trigrams from the tokenized text.
3. Handle out-of-vocabulary (OOV) words:
 * Replace rare words (those occurring fewer than a threshold, e.g., 5
times) with an < OOV > token.
4. Remove stopwords if they’re irrelevant to your analysis (Optional).

Deliverables:
 * A summary of the cleaning and preprocessing steps you applied.
 * A sample output showing tokenized text and generated trigrams.

In [ ]:
"""
    Generate n-grams while ignoring specified tokens.

    Args:
        tokens (list): List of words or tokens.
        n (int): The n in n-grams (e.g., 2 for bigrams, 3 for trigrams).
        ignore_tokens (set): Tokens to ignore, e.g., {"<OOV>"}.

    Returns:
        list: List of filtered n-grams.
"""
from nltk.util import ngrams

def generate_filtered_ngrams(tokens, n, ignore_tokens=None):

    if ignore_tokens is None:
        ignore_tokens = set()

    # Filter out ignore tokens from the token list
    filtered_tokens = [token for token in tokens if token not in ignore_tokens]

    # Generate n-grams
    return list(ngrams(filtered_tokens, n))

In [ ]:
# Tokenization using word_tokenize - Split sentences into tokens using word using
# cleaned text.

# Tokenization using NLTK's word_tokenize (faster for large text)
word_tokens = nltk.word_tokenize(cleaned_text)

print("Tokenized Text (50 elements for print only):\n")
print(word_tokens[:50])
print("\n")

# Remove stopwords
stop_words = set(stopwords.words('english'))
filtered_tokens = [word for word in word_tokens if word not in stop_words]

print("Tokenized Text: Stop words removed(50 elements for print only):\n")
print(filtered_tokens[:50])
print("\n")

# Count the frequency of each word in the text (this helps optimize OOV handling)
word_freq = Counter(filtered_tokens)

sorted_word_counts = sorted(word_freq.items(), key=lambda x: x[1])
print(sorted_word_counts)

# Handle OOV (replace words occurring fewer than a threshold with <OOV>)
threshold = 50
ignore_tokens = {"<OOV>"}

# Replace rare words (those occurring fewer than a threshold) with <OOV>.
processed_filtered_tokens = [filtered_tokens if word_freq[filtered_tokens] > threshold else "<OOV>" for filtered_tokens in filtered_tokens]

print("Processed Tokenized Text (50 elements for print only):\n")
print(processed_filtered_tokens[:50])
print("\n")

# Count the frequency of each word in the text (this helps optimize OOV handling)
word_freq = Counter(processed_filtered_tokens)

sorted_word_counts = sorted(word_freq.items(), key=lambda x: x[1])
print(sorted_word_counts)

# Generate trigrams ignoring <OOV>
processed_trigrams = generate_filtered_ngrams(processed_filtered_tokens, n=3, ignore_tokens=ignore_tokens)

# Count processed trigrams
processed_trigram_counts = Counter(processed_trigrams)

# Select the top 10 most frequent trigrams
top_10_processed_trigrams = processed_trigram_counts.most_common(20)

# Display processed trigrams
print("Top 10 Processed Trigrams with OOV Handling:\n")
for trigram, count in top_10_processed_trigrams:
    print(f'{trigram}: {count}')
print("\n\n")

# Create a DataFrame for plotting
top_10_trigram_df = pd.DataFrame(top_10_processed_trigrams, columns=['Trigram', 'Frequency'])

# Ensure 'Trigram' is a string and not a tuple, just for extra safety
top_10_trigram_df['Trigram'] = top_10_trigram_df['Trigram'].astype(str)

# Plotting the top 10 most frequent trigrams with OOV handling
plt.figure(figsize=(10,6))
sns.barplot(y='Trigram', x='Frequency', data=top_10_trigram_df)
plt.xticks(rotation=45, ha='right')
plt.title("Top 10 Processed Trigrams with OOV Handling")
plt.tight_layout()  # Adjust layout for better display
plt.show()

Tokenized Text (50 elements for print only):

['the', 'canadian', 'society', 'of', 'soil', 'science', 'csss', 'is', 'a', 'nongovernmental', 'nonprofit', 'organization', 'for', 'scientists', 'engineers', 'technologists', 'administrators', 'and', 'students', 'involved', 'in', 'professional', 'soil', 'science', 'its', 'goal', 'is', 'to', 'nurture', 'the', 'discipline', 'of', 'soil', 'science', 'in', 'canada', 'ralitsa', 'b', 'vassileva', 'bulgarian', 'born', 'june', 'is', 'a', 'bulgarian', 'journalist', 'currently', 'she', 'is', 'lecturer']


Tokenized Text: Stop words removed(50 elements for print only):

['canadian', 'society', 'soil', 'science', 'csss', 'nongovernmental', 'nonprofit', 'organization', 'scientists', 'engineers', 'technologists', 'administrators', 'students', 'involved', 'professional', 'soil', 'science', 'goal', 'nurture', 'discipline', 'soil', 'science', 'canada', 'ralitsa', 'b', 'vassileva', 'bulgarian', 'born', 'june', 'bulgarian', 'journalist', 'currently', 'lecturer

**ADD EXPLANANTIN and STEPS HERE...**















-------------------------------------------------------------------------------

Step 3: Model & Understanding (4 marks)

What to Do:
1. Build a trigram language model:
 * Use the counts from your trigrams to estimate probabilities of
sequences.
 * For a given sentence, compute its probability using the trigram model.
2. Evaluate your model using perplexity:
 * Perplexity measures how well a probability model predicts a sample. The
lower the perplexity, the better your model.
* Formula for perplexity:
3. Explain why perplexity is a suitable metric for language models.

Deliverables:
 * A function to compute sentence probabilities using your trigram model.
 * A computed perplexity score for a test dataset.
 * A short paragraph explaining the results and the significance of perplexity.


In [ ]:
# Generate trigrams from tokens
trigrams = generate_filtered_ngrams(processed_filtered_tokens, n=3, ignore_tokens=ignore_tokens)

# Count the frequency of each trigram
trigram_counts = Counter(trigrams)

# Count the frequency of each bigram (for normalization)
bigrams = generate_filtered_ngrams(processed_filtered_tokens, n=2, ignore_tokens=ignore_tokens)
bigram_counts = Counter(bigrams)

# Function to calculate the probability of a trigram
def trigram_probability(trigram):
    bigram = trigram[:2]
    return trigram_counts[trigram] / bigram_counts[bigram]

# Function to calculate the probability of a sentence using the trigram model
def sentence_probability(sentence):
    sentence_tokens = sentence.split()
    sentence_trigrams = list(nltk.ngrams(sentence_tokens, 3))
    probability = 1.0
    for trigram in sentence_trigrams:
        probability *= trigram_probability(trigram)
    return probability

# Example sentence
sentence = "canadian society of soil science"

# Calculate the probability of the example sentence using the trigram model
sentence_prob = sentence_probability(sentence)

print(f"Probability of the sentence '{sentence}': {sentence_prob}")